# Práctica 3: Representación del conocimiento

SOLUCIÓN

El objetivo de esta práctica es aplicar los conceptos teóricos vistos en clase en el módulo de Representación de conocimiento. La práctica consta de un único notebook que se entregará en la tarea de entrega habilitada en el Campus  Virtual.

Cada consulta debe contener breves comentarios que expliquen cada tripleta. __No se valorarán consultas sin explicaciones__.

__Número de grupo: K__

__Nombres de los estudiantes: Lucía Alonso Mozo y Javier Amado Lázaro__

## Consultas SPARQL sobre Wikidata.

En esta práctica vamos a usar el [punto de acceso SPARQL](https://query.wikidata.org/) de Wikidata para contestar las preguntas que se formulan a continuación. Cada pregunta debe ser respondida realizando una única consulta SPARQL. Para cada una de las entidades recuperadas se mostrará __tanto su identificador como su etiqueta__ (nombre de la entidad en lenguaje natural).

Para cada una de las preguntas debes mostrar tanto la consulta como la respuesta obtenida. Si lo consideras necesario, puedes añadir celdas adicionales en formato _Markdown_ para explicar decisiones que hayas tomado al crear la consulta o cualquier otro dato que consideres interesante.

Para resolver estas consultas puedes usar __dos recursos que te recomendamos consultar__ son:

- [Este tutorial de SPARQL](https://www.wikidata.org/wiki/Wikidata:SPARQL_tutorial).
- [Esta recopilación de ejemplos](https://www.wikidata.org/wiki/Wikidata:SPARQL_query_service/queries/examples)

In [2]:
## Lo primero sería instalar en tu entorno de Python wdsparql
## Si no lo tienes instalado, puedes hacerlo desde el notebook
import sys

!{sys.executable} -m pip install wdsparql

# Asumismos instalado wdsparql
%load_ext autoreload
%load_ext wdsparql
%autoreload 2


[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: pip install --upgrade pip


### Ejemplo

Recuperar todas las instancias directas de la clase [Cabra (Q2934)](https://www.wikidata.org/wiki/Q2934) que aparecen en la base de conocimiento.

In [2]:
%%wdsparql
SELECT ?item ?itemLabel
WHERE
{
  ?item wdt:P31 wd:Q2934.  # instancias directas de la clase Cabra
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 1

[Stephen King (Q39829)](https://www.wikidata.org/wiki/Q39829) es un escritor estadounidense de novelas de terror, ficción sobrenatural, misterio, ciencia ficción y literatura fantástica.

Vamos a comenzar por averiguar su fecha y lugar de nacimiento (localidad y país al que pertenece la localidad en la actualidad).

In [2]:
%%wdsparql
SELECT ?birthDateLabel ?birthLocationLabel ?birthLocation ?birthCountryLabel ?birthCountry
WHERE {
  wd:Q39829 wdt:P569 ?birthDate; #cogemos la fecha de nacimiento
            wdt:P19 ?birthLocation. #tomamos la localización de nacimiento
  ?birthLocation wdt:P17 ?birthCountry. #vemos a qué pais pertenece esa localidad
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 2

A continuación vamos a averiguar todas las distintas profesiones (ocupaciones) que se le reconocen en la base de conocimiento. Queremos obtener los resultados ordenados alfabéticamente por el nombre de la profesión.

In [3]:
%%wdsparql
SELECT ?ocupationsLabel ?ocupations
WHERE {
  wd:Q39829 wdt:P106 ?ocupations. #averiguamos las profesiones de Stephen King
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ?ocupationsLabel

### Consulta 3

De todas esas profesiones, ¿cuáles corresponden con subtipos de [Escritor (Q36180)](https://www.wikidata.org/wiki/Q36180)? Ten en cuenta que la jerarquía de tipos de escritores puede ser muy sofisticada.

Puede que [esto](https://www.wikidata.org/wiki/Wikidata:SPARQL_tutorial#Property_paths) te resulte útil.

In [4]:
%%wdsparql
SELECT ?ocupationsLabel ?ocupations
WHERE {
  wd:Q39829 wdt:P106 ?ocupations. #misma consulta que antes
  ?ocupations wdt:P279+ wd:Q36180 #de las ocupaciones tomamos las que son subtipos de escritor (Q36180)
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ?ocupationsLabel

Si no añadimos el `+` a la relación `wdt:P279` muchas de las profesiones no se recuperan.

### Consulta 4

King se ha casado una vez, con Tabitha Spruce, con la que tiene varios hijos. Queremos conocer los nombres de esos hijos y sus fechas de nacimiento (si están disponibles). Los resultados deben aparecer ordenados cronológicamente.

In [5]:
%%wdsparql
SELECT ?childLabel ?child ?bornDateLabel
WHERE
{
  ?child wdt:P22 wd:Q39829; #tomamos los nombres de los hijos de Stephen King
         wdt:P25 wd:Q284287. # de esos seleccionamos aquellos cuya madre sea Tabitha Spruce
  OPTIONAL {?child wdt:P569 ?bornDate} #guardamos las fechas de nacimiento (en el caso de que la tenga, OPTIONAL)
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ASC(?bornDate) #ordenamos cronologicamente

### Consulta 5

King ha recibido muchos premios a lo largo de su carrera. Queremos obtener la lista de premios y, para cada uno de ellos, la fecha en la que fue premiado (si está disponible) y la obra premiada (si está disponible). Los resultados se deben mostrar ordenados por fecha.

Para resolver esta consulta necesitarás acceder a los cualificadores de nodos sentencia y necesitarás entender los prefijos que usa Wikidata. Puede que [esto](https://www.wikidata.org/wiki/Wikidata:SPARQL_tutorial#Qualifiers) te resulte útil.

In [6]:
%%wdsparql
SELECT ?prizeLabel ?prize ?datePrizeLabel ?obraLabel ?obra
WHERE
{
   wd:Q39829  p:P166 ?statement. #tomamos los premios que ha recibido S.K
   ?statement ps:P166 ?prize.
   OPTIONAL {
    ?statement pq:P585 ?datePrize; #cogemos la fecha
           pq:P1686 ?obra #cogemos el nombre de la obra por la que le dieron el premio
  }      
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ASC(?datePrizeLabel)

### Consulta 6

King es sin duda un autor prolífico. ¿Cuántas obras ha escrito a lo largo de su vida? Vamos a considerar sólo instancias directas de [literary work (Q7725634)](https://www.wikidata.org/wiki/Q7725634).

Esta consulta hay dos formas de hacerla. Tomando todos los trabajos que aparecen de Stephen King, y de ellos seleccionar los que son instancias directas de literary work, obteniendo como resultado un total de 34 obras. O, tomando todas las obras registradas, las que son instancias directas de literary work, y luego seleccionar las que fueron escritas por Stephen King, con un total de 226 obras. 
A continuación adjuntamos ambas formas respectivamente. 

In [7]:
%%wdsparql
SELECT (COUNT(?literaryWork) AS ?count)
WHERE
{
    wd:Q39829 wdt:P800 ?literaryWork. #seleccionamos todo lo que SK escribio
    ?literaryWork wdt:P31 wd:Q7725634. #instancias de literary work    
}

In [8]:
%%wdsparql
SELECT (COUNT(DISTINCT ?obras) AS ?count)
WHERE
{
   ?obras wdt:P50 wd:Q39829; #seleccionamos todas las obras escritas por Stephen King
    wdt:P31 wd:Q7725634. # de ellas solo nos quedamos con las instancias directas de literary work
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 7

Aunque King es mundialmente conocido por sus obras de ficción ([Q8253](https://www.wikidata.org/wiki/Q8253)), es también autor de algunas obras menos conocidas de no-ficción ([Q213051](https://www.wikidata.org/wiki/Q213051)). Queremos saber cuáles son estas obras de no-ficción (o cualquiera de sus subgéneros) y su tipo. Los resultados se deben mostrar ordenados por nombre.

No pasa nada si en el resultado aparecen mezclados novelas, relatos, colecciones...

In [9]:
%%wdsparql
SELECT DISTINCT ?obras ?obrasLabel ?tipoLabel ?tipo
WHERE
{
   ?obras wdt:P50 wd:Q39829; #tomamos todas las obras escritas por SK
          wdt:P136/wdt:P279* wd:Q213051; #de ellas selecionamos sus géneros, y nos quedamos con los que son subgeneros de no-ficción
          wdt:P31 ?tipo #tomamos qué tipo de obra son haciendo uso de instancia.
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY (?obrasLabel) #ordenado por el nombre de las obras

### Consulta 8

De todas las obras que ha publicado, queremos recuperar los nombres y fechas de publicación de aquellas escritas entre 1970 y 1980. Si alguna obra tiene varias fechas de publicación, se mostrará si alguna de ellas está dentro de ese periodo.

Puede que [esto](https://www.wikidata.org/wiki/Wikidata:SPARQL_tutorial#FILTER) te resulte útil.

In [10]:
%%wdsparql
SELECT ?obrasLabel ?obras ?fechaObras
WHERE
{
   ?obras wdt:P50 wd:Q39829; #recuperamos los nombres de todas sus obras
         wdt:P577 ?fechaObras. #tomamos las fechas de esas obras
   FILTER(YEAR(?fechaObras)>=1970 && YEAR(?fechaObras)<1980). #filtramos para quedarnos con las que la fecha de publicación está entre 1970 y 1980
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 9

Wikidata contiene información actualizada que en ocasiones incluye futuros lanzamientos u obras planificadas. Vamos a dejar por un momento a King y vamos a considerar la obra de otro famoso autor, George R. R. Martin.

[George R. R. Martin (Q181677)](https://www.wikidata.org/wiki/Q181677) es un escritor de fantasía estadounidense conocido sobre todo por su saga "Canción de hielo y fuego". Martin tiene inconclusa la saga y queremos saber si hay alguna información sobre los libros pendientes. Estos serán sus obras sin fecha de publicación asociada. ¿Aparecen? Si lo hacen, ¿cuántas y cuáles son sus títulos? ¿Hay alguna obra pendiente que no sea de esa saga?

Como se hacen muchas preguntas pero tan solo podemos responder con una consulta, hemos decidido imprimir todas las obras pendientes que tiene George, y para poder distinguir si es de la saga "Cancion de hielo y fuego", imprimimos la saga relacionada con cada obra. Para saber cuántas hay, haremos uso de la columna de la izquierda que nos muestra que son 4.

In [11]:
%%wdsparql
SELECT ?obrasLabel ?obras ?sagaLabel ?saga
WHERE
{
   ?obras wdt:P50 wd:Q181677; #tomamos todas las obras de George R.R Martin
          wdt:P179 ?saga. # de cada obra nos quedamos con la saga
   FILTER NOT EXISTS {
      ?obras wdt:P577 ?fecha # nos quedamos solo con las obras que no tengan fecha
   }
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 10

Volvemos de nuevo a King. De todas las obras que ha publicado (independientemente de su tipo y género), queremos recuperar los nombres y fechas de publicación de aquellas escritas en coautoría, así como los nombnres de estos coautores.

In [13]:
%%wdsparql
SELECT ?obrasLabel ?autoresLabel ?fecha
WHERE
{
   ?obras wdt:P50 wd:Q39829, #tomamos las obras
                  ?autores; #sus respectivos autores
          wdt:P577 ?fecha. #de cada obra tomamos su fecha de publicación
   FILTER(?autores != wd:Q39829). #filtramos aquellas cuyos autores no sean Stephen King, que implicará que son coautores.
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 11

¿Con cuántos coautores diferentes ha trabajado King, independientemente del tipo y género de la obra?

In [14]:
%%wdsparql
SELECT (COUNT(DISTINCT ?autores) AS ?count) #Misma idea que antes pero seleccionamos cuantos autores son distintos de toda la lista.
WHERE
{
   ?obras wdt:P50 wd:Q39829,
                  ?autores;
   FILTER(?autores != wd:Q39829).
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

### Consulta 12

¿Qué otros personajes famosos nacieron el mismo año que King y tienen su misma nacionalidad? Para cada uno de ellos muestra su nombre y ocupación. Muestra los resultados ordenados por nombre, fecha de nacimiento y ocupación.

In [3]:
%%wdsparql
SELECT ?name ?nameLabel ?ocupations ?ocupationsLabel
WHERE
{
   wd:Q39829 wdt:P27 ?nacionalidadSK;
             wdt:P569 ?fechaSK.
  
   BIND(YEAR(?fechaSK) as ?yearSK). 
 
   ?name wdt:P27 ?nacionalidadSK; 
            wdt:P569 ?fechaNacimiento.
        
   FILTER(YEAR(?fechaNacimiento) = ?yearSK && ?name != wd:Q39829). #quitamos a SK y nos quedamos con las personas nacidas el mismo año que el
   OPTIONAL {?name wdt:P106 ?ocupations}.
  
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ?nameLabel ?fechaNacimiento ?ocupations

### Consulta 13

¿Qué otros personajes famosos incluyen King en su nombre completo (name in native language, P1559)? Para cada uno de ellos muestra su nombre, fecha de nacimiento, ocupación y nacionalidad. Muestra los resultados ordenados por nombre, fecha de nacimiento y ocupación.

In [15]:
%%wdsparql
SELECT ?famosos ?famososLabel ?fecha ?ocupacion ?ocupacionLabel ?nacionalidad ?nacionalidadLabel
WHERE
{
   ?famosos wdt:P1559 ?g.
   FILTER regex(?g, "King", "i"). #filtramos los nombres y nos quedamos con aquellos que incluyan king
   FILTER(?famosos != wd:Q39829).  #quitamos a SK
   ?famosos wdt:P569 ?fecha; wdt:P106 ?ocupacion; wdt:P27 ?nacionalidad #cogemos fecha de nacimiento, ocupacion y nacionalidad
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}
ORDER BY ?famososLabel ?fecha ?ocupacionLabel #ordenamos por nombre, fecha de nacimiento y ocupacion


### Consulta 14

¿Cuántos asertos hay sobre King en Wikidata? Ten en cuenta que puede aparecer tanto como sujeto como objeto de una tripleta.

In [16]:
%%wdsparql
SELECT (COUNT(*) AS ?count) #contamos cuantos asertos hay sobre King en Wikidata
WHERE
{
  { ?sujeto ?propiedad1 wd:Q39829 } UNION { wd:Q39829 ?propiedad2 ?objeto } #unimos las veces que King sale como sujeto o como objeto en una tripleta.
   SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
}

__Fecha de las consultas: 21 de abril de 2022__